## Tech Challenge 4
### O Problema
Você foi contratado(a) para uma consultoria, e seu trabalho envolve
analisar os dados de preço do petróleo brent, que pode ser encontrado [no site
do ipea.](http://www.ipeadata.gov.br/ExibeSerie.aspx?module=m&serid=1650971490&oper=view) Essa base de dados histórica envolve duas colunas: data e preço (em
dólares).
Um grande cliente do segmento pediu para que a consultoria
desenvolvesse um dashboard interativo para gerar insights relevantes para
tomada de decisão. Além disso, solicitaram que fosse desenvolvido um modelo
de Machine Learning para fazer o forecasting do preço do petróleo

## Extracting data, initial checks and creating test and train datasets



In [ ]:
# Importações necessárias para análise de séries temporais e machine learning
import pandas as pd  # Biblioteca para manipulação de dados
import matplotlib.pyplot as plt  # Biblioteca para visualização de dados

# Importações específicas do Prophet para análise de séries temporais
from prophet.diagnostics import cross_validation  # Função para validação cruzada
from prophet import Prophet  # Classe principal do Prophet para previsão
from prophet.plot import plot_plotly, plot_components_plotly  # Funções de visualização

# Importações para métricas de avaliação
from sklearn import metrics  # Métricas de avaliação do scikit-learn
from statsmodels.tools.eval_measures import rmse  # Função para cálculo do RMSE

# Importações adicionais do Prophet para diagnóstico
from prophet.diagnostics import cross_validation  # Validacão cruzada
from prophet.diagnostics import performance_metrics  # Métricas de desempenho

# Importação para serialização de modelos
import joblib  # Biblioteca para salvar e carregar modelos treinados

In [ ]:
# Carrega os dados do arquivo Excel do IPEA sobre petróleo
df = pd.read_excel("/content/IPEA-DadosPetroleo.xlsx")

In [ ]:
# Exibe informações detalhadas sobre o DataFrame
# Mostra:
# - Número de entradas não nulas em cada coluna
# - Tipo de dados de cada coluna
# - Uso de memória do DataFrame
# - Visão geral da estrutura dos dados
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11358 entries, 0 to 11357
Data columns (total 2 columns):
 #   Column                                Non-Null Count  Dtype         
---  ------                                --------------  -----         
 0   Data                                  11358 non-null  datetime64[ns]
 1   Preço - petróleo bruto - Brent (FOB)  11358 non-null  float64       
dtypes: datetime64[ns](1), float64(1)
memory usage: 177.6 KB


In [ ]:
# Verifica a quantidade de valores nulos em cada coluna do DataFrame
# Retorna um resumo estatístico mostrando:
# - Número total de valores faltantes por coluna
# - Auxilia na identificação de dados incompletos
# - Importante para análise de qualidade dos dados
df.isnull().sum()

Data                                    0
Preço - petróleo bruto - Brent (FOB)    0
dtype: int64

In [ ]:
# Ordena o DataFrame pelo índice em ordem decrescente
# Parâmetros:
# - ascending=True: ordena em ordem decrescente (mais recente para mais antigo)
# - inplace=True: modifica o DataFrame original em vez de criar uma cópia
df.sort_index(ascending=True, inplace=True)

# Exibe o DataFrame ordenado
df

Data  Preço - petróleo bruto - Brent (FOB)
0     1987-05-20                                 18.63
1     1987-05-21                                 18.45
2     1987-05-22                                 18.55
3     1987-05-25                                 18.60
4     1987-05-26                                 18.63
...          ...                                   ...
11353 2025-02-04                                 76.58
11354 2025-02-05                                 74.71
11355 2025-02-06                                 74.54
11356 2025-02-07                                 74.68
11357 2025-02-10                                 76.23

[11358 rows x 2 columns]

In [ ]:
# Reinicia o índice do DataFrame
# Parâmetros:
# - drop=True: remove o índice antigo
# - inplace=True: modifica o DataFrame original
df.reset_index(drop=True, inplace=True)
df

Data  Preço - petróleo bruto - Brent (FOB)
0     1987-05-20                                 18.63
1     1987-05-21                                 18.45
2     1987-05-22                                 18.55
3     1987-05-25                                 18.60
4     1987-05-26                                 18.63
...          ...                                   ...
11353 2025-02-04                                 76.58
11354 2025-02-05                                 74.71
11355 2025-02-06                                 74.54
11356 2025-02-07                                 74.68
11357 2025-02-10                                 76.23

[11358 rows x 2 columns]

In [ ]:
# Renomeia as colunas do DataFrame para seguir o formato necessário do Prophet
# Prophet requer colunas específicas:
# - 'ds': coluna de data (date stamp)
# - 'y': coluna com os valores a serem previstos
df.rename(columns={'Data': 'ds',
                  'Preço - petróleo bruto - Brent (FOB)': 'y'},
          inplace=True)

In [ ]:
# Divide os dados em conjuntos de treinamento e teste
# Separa os últimos 180 dias para teste e o resto para treinamento
train = df.iloc[:-180]  # Conjunto de treinamento (todos os dados exceto os últimos 180)
test = df.iloc[-180:]   # Conjunto de teste (últimos 180 dias)

## Using Prophet Model (Version 1)

##### Este modelo serve como baseline para comparação
##### Será usado para avaliar se a adição de eventos especiais melhora significativamente as previsões
###### Permite comparar:
###### - Precisão do modelo sem ajustes
###### - Impacto das datas especiais no desempenho
###### - Diferenças estatisticamente significativas entre os modelos





In [ ]:
# Inicializa o modelo Prophet
model_beta = Prophet()
model_beta.fit(df)  # Treina o modelo com os dados históricos

# Cria um DataFrame para previsões futuras
# Período de 180 dias (aproximadamente 6 meses)
future = model_beta.make_future_dataframe(periods=180)

# Gera previsões para o período futuro
# O resultado incluirá:
# - Previsões (yhat)
# - Intervalos de confiança
# - Componentes do modelo (tendência, sazonalidade)
forecast = model_beta.predict(future)

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmpv26ei9f1/0dnj51bi.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmpv26ei9f1/9l3jg0tz.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.11/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=64969', 'data', 'file=/tmp/tmpv26ei9f1/0dnj51bi.json', 'init=/tmp/tmpv26ei9f1/9l3jg0tz.json', 'output', 'file=/tmp/tmpv26ei9f1/prophet_modelbqtx6wu2/prophet_model-20250216225947.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
22:59:47 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
22:59:55 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


In [ ]:
# Exibe as últimas linhas da tabela de previsão
# Seleciona colunas específicas para visualização:
# - ds: data da previsão
# - yhat: valor previsto
# - yhat_lower: limite inferior do intervalo de confiança
# - yhat_upper: limite superior do intervalo de confiança
forecast[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail()

ds       yhat  yhat_lower  yhat_upper
11533 2025-08-05  94.124608   79.548290  108.751975
11534 2025-08-06  94.070255   80.601028  107.843918
11535 2025-08-07  94.121220   80.416813  108.392809
11536 2025-08-08  94.105255   80.682492  106.921518
11537 2025-08-09  94.375476   79.909875  108.802599

In [ ]:
# Gera um gráfico interativo das previsões usando plotly
# Elementos do gráfico:
# - Linha azul: valores previstos (yhat)
# - Regiões sombreadas: intervalos de incerteza (yhat_lower e yhat_upper)
# - Pontos pretos: valores reais observados no conjunto de dados
plot_plotly(model_beta, forecast)

In [ ]:
# Gera um gráfico interativo mostrando os componentes do modelo
# Elementos do gráfico:
# - Tendência geral da série temporal
# - Sazonalidade anual (variações ao longo do ano)
# - Sazonalidade semanal (variações ao longo da semana)

plot_components_plotly(model_beta, forecast)

/usr/local/lib/python3.11/dist-packages/plotly/io/_json.py:560: UserWarning:

Discarding nonzero nanoseconds in conversion.



### Avaliando Modelo 1

In [ ]:
# Analisa as últimas 180 previsões do modelo
# Extrai apenas os valores previstos (yhat) dos últimos 180 dias
predictions = forecast.iloc[-180:]['yhat']

In [ ]:
# Calcula o Erro Quadrático Médio (RMSE) entre previsões e valores reais
print("Root Mean Squared Error entre atuais and valores previstos: ", rmse(predictions, test['y']))

# Calcula a média dos valores reais no conjunto de teste
print("Mean Value os Test Dataset: ", test['y'].mean())

# Calcula a precisão do modelo como porcentagem
# Fórmula: 100 - (RMSE / média dos valores reais * 100)
accuracy = 100 - ((rmse(predictions, test['y']) / test['y'].mean()) * 100)
print(f"Forecast Accuracy: {accuracy:.2f}%")

Root Mean Squared Error entre atuais and valores previstos:  15.195349976751258
Mean Value os Test Dataset:  78.16588888888889
Forecast Accuracy: 80.56%


## Using Prophet Model (Version 2)

##### Este modelo inclui todas as datas especiais e eventos significativos
##### Permite avaliar o impacto de eventos históricos e atuais no mercado de petróleo.


In [ ]:
# Cria um DataFrame com eventos e crises significativas que afetaram o mercado de petróleo
# Cada registro inclui:
# - holiday: nome do evento
# - ds: data de início do evento
# - lower_window: janela inferior (0 indica início do evento)
# - ds_upper: data de fim do evento

market_disrpt = pd.DataFrame([
    {'holiday': 'guerra_golfo', 'ds': '1990-07-15', 'lower_window': 0, 'ds_upper': '1991-01-31'},
    {'holiday': 'crise_2008', 'ds': '2008-07-07', 'lower_window': 0, 'ds_upper': '2008-12-31'},
    {'holiday': 'oil_crash_2014', 'ds': '2014-06-01', 'lower_window': 0, 'ds_upper': '2014-09-30'},
    {'holiday': 'covid_2020', 'ds': '2020-02-01', 'lower_window': 0, 'ds_upper': '2020-12-31'},
    {'holiday': 'russia_ukraine_war', 'ds': '2022-01-01', 'lower_window': 0, 'ds_upper': '2022-12-31'},
    {'holiday': 'middle_east_tensions', 'ds': '2024-09-10', 'lower_window': 0, 'ds_upper': '2024-10-31'},
    {'holiday': 'us_policy_on_oil_prices', 'ds': '2025-01-20', 'lower_window': 0, 'ds_upper': '2025-01-30'},
])

In [ ]:
# Converte as colunas de data para formato datetime
# Isso é necessário para que o Prophet possa processar corretamente as datas especiais
for date_col in ['ds', 'ds_upper']:
    market_disrpt[date_col] = pd.to_datetime(market_disrpt[date_col])

In [ ]:
# Calcula a duração de cada evento especial em dias
# A duração é calculada como a diferença entre a data final (ds_upper) e inicial (ds)
# O resultado é armazenado na coluna 'upper_window' do DataFrame
market_disrpt['upper_window'] = (market_disrpt['ds_upper'] - market_disrpt['ds']).dt.days
market_disrpt

holiday         ds  lower_window   ds_upper  upper_window
0             guerra_golfo 1990-07-15             0 1991-01-31           200
1               crise_2008 2008-07-07             0 2008-12-31           177
2           oil_crash_2014 2014-06-01             0 2014-09-30           121
3               covid_2020 2020-02-01             0 2020-12-31           334
4       russia_ukraine_war 2022-01-01             0 2022-12-31           364
5     middle_east_tensions 2024-09-10             0 2024-10-31            51
6  us_policy_on_oil_prices 2025-01-20             0 2025-01-30            10

In [ ]:
# Inicializa o modelo Prophet com eventos especiais
# O Prophet requer:
# - Coluna de data chamada 'ds'
# - Coluna de valores chamada 'y'
# - Colunas 'holidays' e 'ds' quando usando eventos
# Todas as datas devem estar no formato datetime
model_beta_rc = Prophet(holidays=market_disrpt)
model_beta_rc = model_beta_rc.fit(df)

# Cria um DataFrame para previsões futuras
# Período de 180 dias (aproximadamente 6 meses)
future2 = model_beta_rc.make_future_dataframe(periods=180)

# Gera previsões usando o modelo com eventos especiais
# O resultado incluirá:
# - Previsões (yhat)
# - Intervalos de confiança
# - Componentes do modelo (tendência, sazonalidade)
forecast2 = model_beta_rc.predict(future2)

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmpv26ei9f1/4nzs2bow.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmpv26ei9f1/5qn52en_.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.11/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=61787', 'data', 'file=/tmp/tmpv26ei9f1/4nzs2bow.json', 'init=/tmp/tmpv26ei9f1/5qn52en_.json', 'output', 'file=/tmp/tmpv26ei9f1/prophet_model7p59cdq5/prophet_model-20250216231118.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
23:11:18 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
23:14:08 - cmdstanpy - INFO - Chain [1] done processing


In [ ]:
# Gera um gráfico interativo das previsões usando o modelo com eventos especiais
# O gráfico mostrará:
# - Linha azul: valores previstos (yhat)
# - Regiões sombreadas: intervalos de confiança
# - Pontos pretos: valores reais observados
# - Marcadores especiais: eventos e crises configurados
plot_plotly(model_beta_rc, forecast2)

In [ ]:
# Gera gráficos interativos mostrando os componentes do modelo
# Inclui:
# - Tendência geral da série temporal
# - Sazonalidade anual (variações ao longo do ano)
# - Sazonalidade semanal (variações ao longo da semana)
# - Efeitos dos eventos especiais configurados
plot_components_plotly(model_beta_rc, forecast2)

/usr/local/lib/python3.11/dist-packages/plotly/io/_json.py:560: UserWarning:

Discarding nonzero nanoseconds in conversion.



In [ ]:
# Analisa as últimas 180 previsões do modelo com eventos especiais
# Extrai apenas os valores previstos (yhat) dos últimos 180 dias
predictions2 = forecast2.iloc[-180:]['yhat']

In [ ]:
# Calcula o Erro Quadrático Médio (RMSE) entre previsões e valores reais
print("Root Mean Squared Error entre atuais and valores previstos: ", rmse(predictions2, test['y']))

# Calcula a média dos valores reais no conjunto de teste
print("Mean Value os Test Dataset: ", test['y'].mean())

# Calcula a precisão do modelo como porcentagem
# Fórmula: 100 - (RMSE / média dos valores reais * 100)
accuracy = 100 - ((rmse(predictions2, test['y']) / test['y'].mean()) * 100)
print(f"Forecast Accuracy: {accuracy:.2f}%")

Root Mean Squared Error entre atuais and valores previstos:  11.696060877571846
Mean Value os Test Dataset:  78.16588888888889
Forecast Accuracy: 85.04%
